In [129]:
from pynq import Overlay
from pynq import DefaultHierarchy
import pynq.lib.dma
from pynq import allocate
import numpy as np
from kamene.all import *


In [130]:
overlay=Overlay('babel_overlay_test.bit')

In [131]:
overlay.ip_dict.keys()

dict_keys(['UDP/udp_meta', 'UDP/udp_data', 'network_stack/ethernet_dma', 'axi_dma_0', 'UDP/udp_stack/ipv4_0', 'UDP/udp_stack/udp_0', 'network_stack/arp_server_subnet_0', 'network_stack/ip_handler_0', 'network_stack/mac_ip_encode_0', 'processing_system7_0'])

In [132]:
overlay.download()

In [90]:
udp_meta = overlay.UDP.udp_meta
udp_data = overlay.UDP.udp_data
ethernet = overlay.network_stack.ethernet_dma
overlay.UDP.udp_stack.ipv4_0.local_ipv4_address_V = 0xDEADBEEF
overlay.UDP.udp_stack.protocol_V = 0x11
overlay.UDP.udp_stack.udp_0.reg_ip_address_V_1 = 0xDEADBEEF
overlay.UDP.udp_stack.udp_0.reg_ip_address_V_2 = 0xDEADBEEF
overlay.UDP.udp_stack.udp_0.reg_ip_address_V_3 = 0xDEADBEEF
overlay.UDP.udp_stack.udp_0.reg_ip_address_V_4 = 0xDEADBEEF
overlay.UDP.udp_stack.udp_0.reg_listen_port_V = 54001
overlay.network_stack.arp_server_subnet_0.myMacAddress_V_1 = 0xEEEEEEEE
overlay.network_stack.arp_server_subnet_0.myMacAddress_V_2 = 0xEEEEEEEE
overlay.network_stack.arp_server_subnet_0.myIpAddress_V = 0xDEADBEEF
overlay.network_stack.ip_handler_0.myIpAddress_V = 0xDEADBEEF
overlay.network_stack.mac_ip_encode_0.myMacAddress_V_1 = 0xEEEEEEEE
overlay.network_stack.mac_ip_encode_0.myMacAddress_V_2 = 0xEEEEEEEE
overlay.network_stack.mac_ip_encode_0.regSubNetMask_V= 0x00FFFFFF
overlay.network_stack.mac_ip_encode_0.regDefaultGateway_V= 0xDEADBEEF

In [91]:
udp_data_buffer_out = allocate(shape=(1), dtype=np.uint64)
udp_metadata_buffer_out = allocate(shape=(32), dtype=np.uint8)
udp_data_buffer_in = allocate(shape=(1), dtype=np.uint64)
udp_metadata_buffer_in = allocate(shape=(4), dtype=np.uint64)
raw_packet_in = allocate(shape=(128), dtype=np.uint8)
raw_packet_out = allocate(shape=(128), dtype=np.uint8)

In [92]:
udp_data_buffer_out[0] = 0xDEADBEEFDEADBEEF
for i in range(32):
    udp_metadata_buffer_out[i] = 0xac

In [134]:
udp_meta.recvchannel.start()
udp_meta.sendchannel.start()
udp_data.recvchannel.start()
udp_data.sendchannel.start()
ethernet.recvchannel.start()
ethernet.sendchannel.start()

In [94]:
udp_meta.sendchannel.transfer(udp_metadata_buffer_out)
udp_data.sendchannel.transfer(udp_data_buffer_out)
udp_meta.sendchannel.wait()
udp_data.sendchannel.wait()

In [135]:
ethernet.recvchannel.transfer(raw_packet_in)
ethernet.recvchannel.wait()

In [136]:
for item in raw_packet_in:
    print('{:02x}'.format(item), end=" ")


ff ff ff ff ff ff 00 00 00 00 00 00 08 06 00 01 08 00 06 04 00 01 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 

In [97]:
packet = Ether(dst='ee:ee:ee:ee:ee:ee')/IP(dst="222.173.190.239")/UDP(dport=54001)
i = 0
for b in bytes(packet):
    raw_packet_out[i] = b
    i+=1
for item in raw_packet_out:
    print('{:02x}'.format(item), end=" ")
ethernet.sendchannel.transfer(raw_packet_out)
udp_meta.recvchannel.transfer(udp_metadata_buffer_in)
udp_data.recvchannel.transfer(udp_data_buffer_in)
ethernet.sendchannel.wait()
udp_meta.recvchannel.wait()
udp_data.recvchannel.wait()

ee ee ee ee ee ee 00 05 6b 01 1a cb 08 00 45 00 00 1c 00 01 00 00 40 11 1b c2 c0 a8 00 c9 de ad be ef 00 35 d2 f1 00 08 cd a8 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 

KeyboardInterrupt: 

In [98]:
for item in udp_data_buffer_in:
    print('{:x}'.format(item), end=" ")
for item in udp_metadata_buffer_in:
    print('{:x}'.format(item), end=" ")

0 0 0 0 0 

In [ ]:
udp_meta.recvchannel.stop()
udp_meta.sendchannel.stop()
udp_data.recvchannel.stop()
udp_data.sendchannel.stop()
ethernet.recvchannel.stop()
ethernet.sendchannel.stop()